# Rollup support

In [1]:
import pandas as pd
from pandas import DataFrame
from data201 import db_connection, df_query

pd.set_option('display.max_rows', None)

In [2]:
conn = db_connection(config_file='students.ini')
cursor = conn.cursor()

## Goal
#### We want to generate a table like the following. The number of stars after each label indicates its subtotal rank, from lowest to highest:
```
DEPARTMENT *
    SCHOOL **
  SEMESTER ***
    YEARLY ****
     GRAND *****
```
#### Examples:
- #### Line 12 `SCHOOL **` is the sum of line 9 `DEPARTMENT *` and line 11 `DEPARTMENT *`: 161 = 76 + 85
- #### Line 13 `SEMESTER ***` is the sum of Line 3 `SCHOOL **` and line 6 `SCHOOL **` and line 12 `SCHOOL **`: 352 = 88 + 103 + 161
```
   school_year semester       school              department          level  TOTAL         LABEL
   ---------------------------------------------------------------------------------------------
0    2022-2023     fall  Engineering  Electrical Engineering       graduate   41.0              
1    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   47.0              
2                                                                             88.0  DEPARTMENT *
3                                                                             88.0     SCHOOL **
4    2022-2023     fall  Information            Data Science       graduate  103.0              
5                                                                            103.0  DEPARTMENT *
6                                                                            103.0     SCHOOL **
7    2022-2023     fall      Science        Computer Science       graduate   27.0              
8    2022-2023     fall      Science        Computer Science  undergraduate   49.0              
9                                                                             76.0  DEPARTMENT *
10   2022-2023     fall      Science   Physics and Astronomy  undergraduate   85.0              
11                                                                            85.0  DEPARTMENT *
12                                                                           161.0     SCHOOL **
13                                                                           352.0  SEMESTER ***
14   2022-2023   spring  Engineering  Electrical Engineering       graduate   38.0              
15   2022-2023   spring  Engineering  Electrical Engineering  undergraduate   51.0              
16                                                                            89.0  DEPARTMENT *
17                                                                            89.0     SCHOOL **
18   2022-2023   spring  Information            Data Science       graduate   99.0              
19                                                                            99.0  DEPARTMENT *
20                                                                            99.0     SCHOOL **
21   2022-2023   spring      Science        Computer Science       graduate   14.0              
22   2022-2023   spring      Science        Computer Science  undergraduate   60.0              
23                                                                            74.0  DEPARTMENT *
24   2022-2023   spring      Science   Physics and Astronomy  undergraduate   82.0              
25                                                                            82.0  DEPARTMENT *
26                                                                           156.0     SCHOOL **
27                                                                           344.0  SEMESTER ***
28                                                                           696.0   YEARLY ****
29   2023-2024     fall  Engineering  Electrical Engineering       graduate   44.0              
30   2023-2024     fall  Engineering  Electrical Engineering  undergraduate   35.0              
31                                                                            79.0  DEPARTMENT *
32                                                                            79.0     SCHOOL **
33   2023-2024     fall  Information            Data Science       graduate   63.0              
34                                                                            63.0  DEPARTMENT *
35                                                                            63.0     SCHOOL **
36   2023-2024     fall      Science        Computer Science       graduate   44.0              
37   2023-2024     fall      Science        Computer Science  undergraduate   41.0              
38                                                                            85.0  DEPARTMENT *
39   2023-2024     fall      Science   Physics and Astronomy  undergraduate   44.0              
40                                                                            44.0  DEPARTMENT *
41                                                                           129.0     SCHOOL **
42                                                                           271.0  SEMESTER ***
43                                                                           271.0   YEARLY ****
44                                                                           967.0   GRAND *****
```

## Window functions
#### We can use window functions to display all the subtotals and the grand total.

In [3]:
df_query(conn, 
    """
    SELECT DISTINCT 
        school_year, semester, school, department, level,
        SUM(count) OVER() 
            AS grand_total,
        SUM(count) OVER(PARTITION BY school_year) 
            AS yearly_total,
        SUM(count) OVER(PARTITION BY school_year, semester) 
            AS semester_total,
        SUM(count) OVER(PARTITION BY school_year, semester, school) 
            AS school_total,
        SUM(count) OVER(PARTITION BY school_year, semester, 
                                    school, department) 
            AS dept_total,
        SUM(count) OVER(PARTITION BY school_year, semester, 
                                    school, department, level) 
            AS level_total
    FROM counts
    JOIN calendar
      ON counts.when = calendar.key
    JOIN classes
      ON counts.which = classes.key
    ORDER BY school_year, semester, school, department, level
    """
)

school_year semester       school              department          level  \
0    2022-2023     fall  Engineering  Electrical Engineering       graduate   
1    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   
2    2022-2023     fall  Information            Data Science       graduate   
3    2022-2023     fall      Science        Computer Science       graduate   
4    2022-2023     fall      Science        Computer Science  undergraduate   
5    2022-2023     fall      Science   Physics and Astronomy  undergraduate   
6    2022-2023   spring  Engineering  Electrical Engineering       graduate   
7    2022-2023   spring  Engineering  Electrical Engineering  undergraduate   
8    2022-2023   spring  Information            Data Science       graduate   
9    2022-2023   spring      Science        Computer Science       graduate   
10   2022-2023   spring      Science        Computer Science  undergraduate   
11   2022-2023   spring      Science   Physics and Astronomy  undergraduate   
12   2023-2024     fall  Engineering  Electrical Engineering       graduate   
13   2023-2024     fall  Engineering  Electrical Engineering  undergraduate   
14   2023-2024     fall  Information            Data Science       graduate   
15   2023-2024     fall      Science        Computer Science       graduate   
16   2023-2024     fall      Science        Computer Science  undergraduate   
17   2023-2024     fall      Science   Physics and Astronomy  undergraduate   

    grand_total  yearly_total  semester_total  school_total  dept_total  \
0         967.0         696.0           352.0          88.0        88.0   
1         967.0         696.0           352.0          88.0        88.0   
2         967.0         696.0           352.0         103.0       103.0   
3         967.0         696.0           352.0         161.0        76.0   
4         967.0         696.0           352.0         161.0        76.0   
5         967.0         696.0           352.0         161.0        85.0   
6         967.0         696.0           344.0          89.0        89.0   
7         967.0         696.0           344.0          89.0        89.0   
8         967.0         696.0           344.0          99.0        99.0   
9         967.0         696.0           344.0         156.0        74.0   
10        967.0         696.0           344.0         156.0        74.0   
11        967.0         696.0           344.0         156.0        82.0   
12        967.0         271.0           271.0          79.0        79.0   
13        967.0         271.0           271.0          79.0        79.0   
14        967.0         271.0           271.0          63.0        63.0   
15        967.0         271.0           271.0         129.0        85.0   
16        967.0         271.0           271.0         129.0        85.0   
17        967.0         271.0           271.0         129.0        44.0   

    level_total  
0          41.0  
1          47.0  
2         103.0  
3          27.0  
4          49.0  
5          85.0  
6          38.0  
7          51.0  
8          99.0  
9          14.0  
10         60.0  
11         82.0  
12         44.0  
13         35.0  
14         63.0  
15         44.0  
16         41.0  
17         44.0

## Problems with using the window functions
- #### Extra columns
- #### Repeated subtotals values
- #### Hard to read

## `GROUP BY ... WITH ROLLUP`
#### The `GROUP BY` clause creates the drill-down hierarchy `school_year`, `semester`, `school`, `department`, `level`, and `class`. Adding `WITH ROLLUP` to the clause tells `SUM(count)` to calculate subtotals by drilling up the hierarchy ranks: level, department, school, semester, and year. In a row that contains a subtotal at a particular hierarchy rank, the field value whose subtotals were added are next to the leftmost None in the dataframe. Add the subtotals of the rows whose leftmost None is one column to the right, and are therefore one rank lower. Examples from the calculated dataframe displayed below:
- #### Line 6: Electrical Engineering is next to the leftmost None. 88 = 41 + 47 (lines 2 and 5) is the subtotal of all the Electrical Engineering classes.
- #### Line 25: Science is next to the leftmost None. 161 = 76 + 85 (lines 20 and 24) is the subtotal of the School of Science.

In [4]:
df_query(conn, 
    """
    SELECT school_year, semester, school, department, level, class, 
           SUM(count) AS SUBTOTALS
    FROM counts
    JOIN calendar
      ON counts.when = calendar.key
    JOIN classes
      ON counts.which = classes.key
    GROUP BY school_year, semester, school, department, level, class
    WITH ROLLUP
    """
)

school_year semester       school              department          level  \
0    2022-2023     fall  Engineering  Electrical Engineering       graduate   
1    2022-2023     fall  Engineering  Electrical Engineering       graduate   
2    2022-2023     fall  Engineering  Electrical Engineering       graduate   
3    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   
4    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   
5    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   
6    2022-2023     fall  Engineering  Electrical Engineering           None   
7    2022-2023     fall  Engineering                    None           None   
8    2022-2023     fall  Information            Data Science       graduate   
9    2022-2023     fall  Information            Data Science       graduate   
10   2022-2023     fall  Information            Data Science       graduate   
11   2022-2023     fall  Information            Data Science       graduate   
12   2022-2023     fall  Information            Data Science           None   
13   2022-2023     fall  Information                    None           None   
14   2022-2023     fall      Science        Computer Science       graduate   
15   2022-2023     fall      Science        Computer Science       graduate   
16   2022-2023     fall      Science        Computer Science       graduate   
17   2022-2023     fall      Science        Computer Science  undergraduate   
18   2022-2023     fall      Science        Computer Science  undergraduate   
19   2022-2023     fall      Science        Computer Science  undergraduate   
20   2022-2023     fall      Science        Computer Science           None   
21   2022-2023     fall      Science   Physics and Astronomy  undergraduate   
22   2022-2023     fall      Science   Physics and Astronomy  undergraduate   
23   2022-2023     fall      Science   Physics and Astronomy  undergraduate   
24   2022-2023     fall      Science   Physics and Astronomy           None   
25   2022-2023     fall      Science                    None           None   
26   2022-2023     fall         None                    None           None   
27   2022-2023   spring  Engineering  Electrical Engineering       graduate   
28   2022-2023   spring  Engineering  Electrical Engineering       graduate   
29   2022-2023   spring  Engineering  Electrical Engineering       graduate   
30   2022-2023   spring  Engineering  Electrical Engineering  undergraduate   
31   2022-2023   spring  Engineering  Electrical Engineering  undergraduate   
32   2022-2023   spring  Engineering  Electrical Engineering  undergraduate   
33   2022-2023   spring  Engineering  Electrical Engineering           None   
34   2022-2023   spring  Engineering                    None           None   
35   2022-2023   spring  Information            Data Science       graduate   
36   2022-2023   spring  Information            Data Science       graduate   
37   2022-2023   spring  Information            Data Science       graduate   
38   2022-2023   spring  Information            Data Science       graduate   
39   2022-2023   spring  Information            Data Science           None   
40   2022-2023   spring  Information                    None           None   
41   2022-2023   spring      Science        Computer Science       graduate   
42   2022-2023   spring      Science        Computer Science       graduate   
43   2022-2023   spring      Science        Computer Science  undergraduate   
44   2022-2023   spring      Science        Computer Science  undergraduate   
45   2022-2023   spring      Science        Computer Science  undergraduate   
46   2022-2023   spring      Science        Computer Science           None   
47   2022-2023   spring      Science   Physics and Astronomy  undergraduate   
48   2022-2023   spring      Science   Physics and Astronomy  undergraduate   
49   2022-2023   spring      Science   Physics and As

## `GROUPING()` function
#### The `GROUPING()` function takes a field as its argument, and it returns 1 if the field value is `NULL` due to `ROLLUP` subtotaling. Otherwise, it return 0 for any other value, including `NULL` ***not*** generated by subtotaling. We can use these 0 and 1 values in `IF` tests to enhance the dataframe display.
#### The calculated dataframe displayed below shows the values of the `GROUPING()` function. Each 1 corresponds to a `NULL` generated by subtotaling. Note that a `NULL` is represented by `None` in a dataframe display.

In [5]:
df_query(conn, 
    """
    SELECT school_year, semester,
           school, department, level,
           GROUPING(school_year) AS GRAND,
           GROUPING(semester)    AS YEAR,
           GROUPING(school)      AS SEMESTER,
           GROUPING(department)  AS SCHOOL,
           GROUPING(level)       AS DEPT
    FROM counts
    JOIN calendar
      ON counts.when = calendar.key
    JOIN classes
      ON counts.which = classes.key
    GROUP BY school_year, semester, school, department, level 
    WITH ROLLUP
    """
)

school_year semester       school              department          level  \
0    2022-2023     fall  Engineering  Electrical Engineering       graduate   
1    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   
2    2022-2023     fall  Engineering  Electrical Engineering           None   
3    2022-2023     fall  Engineering                    None           None   
4    2022-2023     fall  Information            Data Science       graduate   
5    2022-2023     fall  Information            Data Science           None   
6    2022-2023     fall  Information                    None           None   
7    2022-2023     fall      Science        Computer Science       graduate   
8    2022-2023     fall      Science        Computer Science  undergraduate   
9    2022-2023     fall      Science        Computer Science           None   
10   2022-2023     fall      Science   Physics and Astronomy  undergraduate   
11   2022-2023     fall      Science   Physics and Astronomy           None   
12   2022-2023     fall      Science                    None           None   
13   2022-2023     fall         None                    None           None   
14   2022-2023   spring  Engineering  Electrical Engineering       graduate   
15   2022-2023   spring  Engineering  Electrical Engineering  undergraduate   
16   2022-2023   spring  Engineering  Electrical Engineering           None   
17   2022-2023   spring  Engineering                    None           None   
18   2022-2023   spring  Information            Data Science       graduate   
19   2022-2023   spring  Information            Data Science           None   
20   2022-2023   spring  Information                    None           None   
21   2022-2023   spring      Science        Computer Science       graduate   
22   2022-2023   spring      Science        Computer Science  undergraduate   
23   2022-2023   spring      Science        Computer Science           None   
24   2022-2023   spring      Science   Physics and Astronomy  undergraduate   
25   2022-2023   spring      Science   Physics and Astronomy           None   
26   2022-2023   spring      Science                    None           None   
27   2022-2023   spring         None                    None           None   
28   2022-2023     None         None                    None           None   
29   2023-2024     fall  Engineering  Electrical Engineering       graduate   
30   2023-2024     fall  Engineering  Electrical Engineering  undergraduate   
31   2023-2024     fall  Engineering  Electrical Engineering           None   
32   2023-2024     fall  Engineering                    None           None   
33   2023-2024     fall  Information            Data Science       graduate   
34   2023-2024     fall  Information            Data Science           None   
35   2023-2024     fall  Information                    None           None   
36   2023-2024     fall      Science        Computer Science       graduate   
37   2023-2024     fall      Science        Computer Science  undergraduate   
38   2023-2024     fall      Science        Computer Science           None   
39   2023-2024     fall      Science   Physics and Astronomy  undergraduate   
40   2023-2024     fall      Science   Physics and Astronomy           None   
41   2023-2024     fall      Science                    None           None   
42   2023-2024     fall         None                    None           None   
43   2023-2024     None         None                    None           None   
44        None     None         None                    None           None   

    GRAND  YEAR  SEMESTER  SCHOOL  DEPT  
0       0     0         0       0     0  
1       0     0         0       0     0  
2       0     0         0       0     1  
3       0     0         0       1     1  
4       0     0         0       0     0  
5       0     0         0       0     1  
6       0     0         0       1     1  
7       0     0         0       

## Total student counts with embedded labels
#### We use the results of calling the `GROUPING()` function to display subtotal labels. In a row with more than one label, the leftmost label says at which hierarchy rank the subtotal was calculated. Examples from the dataframe displayed below:
- #### Line 6: 103 is the subtotal of the Information school.
- #### Line 13: 352 is the subtotal of the fall semester.

In [6]:
labels = ('     GRAND *****', 
          '    YEARLY **** ', 
          '  SEMESTER ***  ', 
          '    SCHOOL **   ', 
          'DEPARTMENT *    ')

grand, yearly, semester, school, department = \
    (label for label in labels)

In [7]:
df = df_query(conn, 
   f"""
    SELECT 
        --      ---------            ----             -----
        --      CONDITION            TRUE             FALSE
        --      ---------            ----             -----
        IF (GROUPING(school_year), '{grand}',       school_year) 
               AS school_year,
        IF (GROUPING(semester),    '{yearly}',      semester) 
               AS semester,
        IF (GROUPING(school),      '{semester}',    school) 
               AS school,
        IF (GROUPING(department),  '{school}',      department) 
               AS department,
        IF (GROUPING(level),       '{department}',  level) 
               AS level,
        SUM(count) AS total
    FROM counts
    JOIN calendar
      ON counts.when = calendar.key
    JOIN classes
      ON counts.which = classes.key
    GROUP BY school_year, semester, school, department, level 
    WITH ROLLUP
    """
)

df.style.format( {'LABEL' : '{:16s}'} )

## Total student counts with side labels
#### The dataframe displayed below contains the same information as the table above, except that it puts the subtotal labels in a column at the right. All the fields of a subtotal row are blank.

In [8]:
df_query(conn, 
   f"""
    SELECT 
        -- For the first 5 columns, print blanks if any colummn value 
        -- is a NULL due to ROLLUP subtotaling.
        
        --      ---------            ----   -----
        --      CONDITION            TRUE   FALSE
        --      ---------            ----   -----
        IF (   GROUPING(school_year)
            OR GROUPING(semester) 
            OR GROUPING(school) 
            OR GROUPING(department) 
            OR GROUPING(level),       '',  school_year)  AS school_year,
            
        IF (   GROUPING(school_year)
            OR GROUPING(semester) 
            OR GROUPING(school) 
            OR GROUPING(department) 
            OR GROUPING(level),       '',  semester)     AS semester,
            
        IF (   GROUPING(school_year)
            OR GROUPING(semester) 
            OR GROUPING(school) 
            OR GROUPING(department) 
            OR GROUPING(level),       '',  school)       AS school,

        IF (   GROUPING(school_year)
            OR GROUPING(semester) 
            OR GROUPING(school) 
            OR GROUPING(department) 
            OR GROUPING(level),       '',  department)   AS department,
            
        IF (   GROUPING(school_year)
            OR GROUPING(semester) 
            OR GROUPING(school) 
            OR GROUPING(department) 
            OR GROUPING(level),       '',  level)        AS level,

        -- The 6th column is subtotals.
        --
        SUM(count) AS SUBTOTAL,

        -- The last column is an appropriate label.
        --
        IF (GROUPING(school_year), '{grand}',
        IF (GROUPING(semester),    '{yearly}',
        IF (GROUPING(school),      '{semester}',
        IF (GROUPING(department),  '{school}',
        IF (GROUPING(level),       '{department}',
        '')))))                                          AS LABEL
                                                   
    FROM counts
    JOIN calendar
      ON counts.when = calendar.key
    JOIN classes
      ON counts.which = classes.key
    GROUP BY school_year, semester, school, department, level 
    WITH ROLLUP
    """
)

school_year semester       school              department          level  \
0    2022-2023     fall  Engineering  Electrical Engineering       graduate   
1    2022-2023     fall  Engineering  Electrical Engineering  undergraduate   
2                                                                             
3                                                                             
4    2022-2023     fall  Information            Data Science       graduate   
5                                                                             
6                                                                             
7    2022-2023     fall      Science        Computer Science       graduate   
8    2022-2023     fall      Science        Computer Science  undergraduate   
9                                                                             
10   2022-2023     fall      Science   Physics and Astronomy  undergraduate   
11                                                                            
12                                                                            
13                                                                            
14   2022-2023   spring  Engineering  Electrical Engineering       graduate   
15   2022-2023   spring  Engineering  Electrical Engineering  undergraduate   
16                                                                            
17                                                                            
18   2022-2023   spring  Information            Data Science       graduate   
19                                                                            
20                                                                            
21   2022-2023   spring      Science        Computer Science       graduate   
22   2022-2023   spring      Science        Computer Science  undergraduate   
23                                                                            
24   2022-2023   spring      Science   Physics and Astronomy  undergraduate   
25                                                                            
26                                                                            
27                                                                            
28                                                                            
29   2023-2024     fall  Engineering  Electrical Engineering       graduate   
30   2023-2024     fall  Engineering  Electrical Engineering  undergraduate   
31                                                                            
32                                                                            
33   2023-2024     fall  Information            Data Science       graduate   
34                                                                            
35                                                                            
36   2023-2024     fall      Science        Computer Science       graduate   
37   2023-2024     fall      Science        Computer Science  undergraduate   
38                                                                            
39   2023-2024     fall      Science   Physics and Astronomy  undergraduate   
40                                                                            
41                                                                            
42                                                                            
43                                                                            
44                                                                            

    SUBTOTAL             LABEL  
0       41.0                    
1       47.0                    
2       88.0  DEPARTMENT *      
3       88.0      SCHOOL **     
4      103.0                    
5      103.0  DEPARTMENT *      
6      103.0      SCHOOL **     
7       27.0                    
8       49.0                    
9       76.0  DEPARTMENT *      
10   

In [9]:
cursor.close()
conn.close()